## Exploratory data analysis of the chocolate rating

---

## Summary of the data set
---

The data set used in this project is a chocolate rating with the tasting effectiveness features created by Brady Brelinski and Andrea Brelinski, the directors of Manhattan Chocolate Society posted on the [Flavors of Cacao](http://flavorsofcacao.com), specifically on this [page](http://flavorsofcacao.com/chocolate_database.html). Each row in the data set represents summary statistics of the chocolate rating(1.0 to 5.0) and the features related to the taste of the chocolate(including the bean origin information, the manufacturer company information and location, the cocoa percentage, ingredients and flavor etc.). The total observations of this data set are $2588$, and $9$ features with our target column "Rating". There are $87$ observations with missing values in the "Ingredients" feature and all other features do not have missing values. Considering our main goal is to find the best-supervised machine learning model to predict the chocolate rating, we will do the basic data wrangling of the data set observations.

### Instructions
---

- Use our download script to download the latest data from [Flavors of Cacao](http://flavorsofcacao.com/chocolate_database.html)
- Read the downloaded CSV to perform data wrangling and exploratory data analysis (EDA)

## Imports and data observations
---

In [1]:
# IMPORT
import numpy as np
import pandas as pd
import altair as alt
from pandas_profiling import ProfileReport

from sklearn.model_selection import train_test_split

In [2]:
# Read raw data files
choco_raw = pd.read_csv("../data/raw/chocolate_raw.csv")
choco_raw.shape

(2588, 10)

- There are 2588 observations with 10 columns (9 features and 1 target).

In [3]:
choco_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2588 entries, 0 to 2587
Data columns (total 10 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   REF                               2588 non-null   int64  
 1   Company (Manufacturer)            2588 non-null   object 
 2   Company Location                  2588 non-null   object 
 3   Review Date                       2588 non-null   int64  
 4   Country of Bean Origin            2588 non-null   object 
 5   Specific Bean Origin or Bar Name  2588 non-null   object 
 6   Cocoa Percent                     2588 non-null   object 
 7   Ingredients                       2501 non-null   object 
 8   Most Memorable Characteristics    2588 non-null   object 
 9   Rating                            2588 non-null   float64
dtypes: float64(1), int64(2), object(7)
memory usage: 202.3+ KB


- 87 missing values are observed in the `Ingredients` column. We will back to handle it later.

In [4]:
alt.Chart(choco_raw).mark_bar().encode(
    x=alt.X('Rating', title='Rating', bin = alt.BinParams(maxbins = 20)),
    y=alt.Y('count()')
).properties(
    width=400,
    height=300
)

alt.Chart(...)

- We can see the target value "Rating" distribution as a continuous variable is in "1.0-4.0" as a right-skewed bell-shaped histogram.

## Partition the data set into training and test set

- To avoid violation of the golden rule, we will split the data set such that 75% of observations are in the training and 25% of observations are in the test set for further data analyzing. That means the train data set will have 1941 observations and the test data set will have 647 observations.

In [5]:
train_df, test_df = train_test_split(choco_raw, test_size=0.25, random_state=522)

In [6]:
train_df

REF  Company (Manufacturer) Company Location  Review Date  \
206    983         Bar Au Chocolat           U.S.A.         2012   
126   1534                   Arete           U.S.A.         2015   
2139  1650                  Sirene           Canada         2015   
1879  1271              Paul Young             U.K.         2014   
916    494                Felchlin      Switzerland         2010   
...    ...                     ...              ...          ...   
796    470                  Domori            Italy         2010   
154   2330                   Arete           U.S.A.         2019   
330    341  Bouga Cacao (Tulicorp)          Ecuador         2009   
407    641            Cacao Prieto           U.S.A.         2011   
1899  2700        Pierre Marcolini          Belgium         2021   

     Country of Bean Origin Specific Bean Origin or Bar Name Cocoa Percent  \
206              Madagascar                        Sambirano           70%   
126                 Ecuador           Puerto Quito, heirloom           70%   
2139                  Haiti                             Pisa           73%   
1879             Madagascar             Madagascar, w/ shell           64%   
916                 Grenada                          Grenada           58%   
...                     ...                              ...           ...   
796               Venezuela         Chuao, Hacienda San Jose           70%   
154                   India                  Jangareddygudem           70%   
330                 Ecuador          El Oro, Hacienda de Oro          100%   
407      Dominican Republic               Dominican Republic           66%   
1899                  China               Hainan, lot 218012           72%   

       Ingredients  Most Memorable Characteristics  Rating  
206         2- B,S            raspberry, mild sour    3.75  
126         2- B,S                    spicy, cocoa    3.75  
2139        2- B,S      oily, medium roasted cocoa    3.25  
1879       2- B,S*     coarse, sweet, tart, earthy    2.75  
916   5- B,S,C,V,L             spicey, marshmallow    3.50  
...            ...                             ...     ...  
796         2- B,S      subtle, caramel, sour milk    3.00  
154       3- B,S,C         herbs, mushroom, acidic    3.25  
330            NaN  cardboard, very bitter, floral    1.50  
407         2- B,S   creamy,blueberry,black pepper    3.75  
1899    4- B,S,C,L            fruity, rich, grassy    3.50  

[1941 rows x 10 columns]

In [7]:
alt.Chart(train_df).mark_bar().encode(
    x=alt.X('Rating', title='Rating', bin = alt.BinParams(maxbins = 20)),
    y=alt.Y('count()')
).properties(
    width=400,
    height=300
)

alt.Chart(...)

- The separated training data set distribution is similar to the original data set as right skewed. In further analysis when applying machine learning, we might consider applying log transform to the target value if the model is being effected a lot by the skewed data.

## Data wrangling

- Spaces in column names are replaced with underscore.
- Missing values are placed with `np.nan` at this point.
- A high level summary of `train_df` is observed by calling `.info()`, followed by `.describe()`.

In [8]:
train_df.columns = train_df.columns.str.replace(' ', '_')
test_df.columns = test_df.columns.str.replace(' ', '_')
train_df['Ingredients'] = train_df['Ingredients'].replace('', np.nan)
test_df['Ingredients'] = test_df['Ingredients'].replace('', np.nan)

In [9]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1941 entries, 206 to 1899
Data columns (total 10 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   REF                               1941 non-null   int64  
 1   Company_(Manufacturer)            1941 non-null   object 
 2   Company_Location                  1941 non-null   object 
 3   Review_Date                       1941 non-null   int64  
 4   Country_of_Bean_Origin            1941 non-null   object 
 5   Specific_Bean_Origin_or_Bar_Name  1941 non-null   object 
 6   Cocoa_Percent                     1941 non-null   object 
 7   Ingredients                       1872 non-null   object 
 8   Most_Memorable_Characteristics    1941 non-null   object 
 9   Rating                            1941 non-null   float64
dtypes: float64(1), int64(2), object(7)
memory usage: 166.8+ KB


- From the above report, we can see the train data set has $1941$ observations in total with $69$ missing values in "Ingredients".
- `Cocoa_Percent` was imported as text. This column is converted to `float`.

In [10]:
train_df['Cocoa_Percent'] = train_df['Cocoa_Percent'].str.rstrip('%').astype('float')
test_df['Cocoa_Percent'] = test_df['Cocoa_Percent'].str.rstrip('%').astype('float')

train_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1941 entries, 206 to 1899
Data columns (total 10 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   REF                               1941 non-null   int64  
 1   Company_(Manufacturer)            1941 non-null   object 
 2   Company_Location                  1941 non-null   object 
 3   Review_Date                       1941 non-null   int64  
 4   Country_of_Bean_Origin            1941 non-null   object 
 5   Specific_Bean_Origin_or_Bar_Name  1941 non-null   object 
 6   Cocoa_Percent                     1941 non-null   float64
 7   Ingredients                       1872 non-null   object 
 8   Most_Memorable_Characteristics    1941 non-null   object 
 9   Rating                            1941 non-null   float64
dtypes: float64(2), int64(2), object(6)
memory usage: 166.8+ KB


In [11]:
train_df.describe(include='all')

REF Company_(Manufacturer) Company_Location  Review_Date  \
count   1941.000000                   1941             1941  1941.000000   
unique          NaN                    534               63          NaN   
top             NaN                   Soma           U.S.A.          NaN   
freq            NaN                     41              879          NaN   
mean    1454.362184                    NaN              NaN  2014.519835   
std      776.460731                    NaN              NaN     4.096421   
min        5.000000                    NaN              NaN  2006.000000   
25%      809.000000                    NaN              NaN  2012.000000   
50%     1466.000000                    NaN              NaN  2015.000000   
75%     2126.000000                    NaN              NaN  2018.000000   
max     2768.000000                    NaN              NaN  2022.000000   

       Country_of_Bean_Origin Specific_Bean_Origin_or_Bar_Name  Cocoa_Percent  \
count                    1941                             1941    1941.000000   
unique                     61                             1288            NaN   
top                 Venezuela                       Madagascar            NaN   
freq                      201                               41            NaN   
mean                      NaN                              NaN      71.641680   
std                       NaN                              NaN       5.582282   
min                       NaN                              NaN      50.000000   
25%                       NaN                              NaN      70.000000   
50%                       NaN                              NaN      70.000000   
75%                       NaN                              NaN      74.000000   
max                       NaN                              NaN     100.000000   

       Ingredients Most_Memorable_Characteristics       Rating  
count         1872                           1941  1941.000000  
unique          20                           1915          NaN  
top       3- B,S,C                   spicy, cocoa          NaN  
freq           769                              4          NaN  
mean           NaN                            NaN     3.197192  
std            NaN                            NaN     0.454977  
min            NaN                            NaN     1.000000  
25%            NaN                            NaN     3.000000  
50%            NaN                            NaN     3.250000  
75%            NaN                            NaN     3.500000  
max            NaN                            NaN     4.000000

From the above tables, we can see that the mean rating value is $3.20$ with the lowest $1.0$ and highest $4.0$, no chocolate gets the highest $5.0$. The highest cocoa percentage is $100$%, the lowest is $50$%, and both the mean and median cocoa percentage is $70$%, which is the most popular cocoa percentage.

## Profiling report

- To have a better understanding of the data, we will generate a profile report to discover the data.

In [12]:
# Uncommend the below code to see the full profilling report
# train_df_profile = ProfileReport(train_df, title="Chocolate Profiling Report")
# train_df_profile.to_notebook_iframe()

- Preliminary analysis based on the profilling report

| Features | Type | Remarks|
---------|------|--------
|REF | numeric | Drop. An identifier carries no information|
|Company_(Manufacturer) | categorical | In spite of 534 distinct classes in 1941 data, may be useful |
|Company_Location | categorical | May be useful (63 distinct classes in 1941 data) |
|Review_Date | numeric | Drop. Not useful|
|Country_of_Bean_Origin | categorical | May be useful (61 distinct classes in 1941 data) |
|Specific_Bean_Origin_or_Bar_Name | categorical | Drop. Too many classes (1288 distinct classes in 1941 data) |
|Cocoa_Percent | numeric | An important feature |
|Ingredients | categorical | Generally a comma-delimited column. Further analysis is required. May / may not need to split. (20 distinct classes) |
|Most_Memorable_Characteristics | categorical | A comma-delimited column. Further analysis is required. Probably need a split. |
|Rating | numeric | Our target |

## Further analysis on `Ingredients` and `Most_Memorable_Characteristics`

- Since these two features carry data in comma-delimited format, we will need to do further splitting in order to have a better understanding for model selecting.

#### **`Ingredients`**

In [13]:
# Analyse Ingredients
# B = Beans, S = Sugar, S* = Sweetener other than white cane or beet sugar, C = Cocoa Butter, V = Vanilla, L = Lecithin, Sa = Salt

# Drop the rows with blank ingredients, remove the first 2 characters which are meaningless, split the comma delimited text
# boom_train_ingredients = choco_raw['Ingredients'].replace('', np.nan)
boom_train_ingredients = train_df['Ingredients']
boom_train_ingredients = boom_train_ingredients.dropna()
boom_train_ingredients = boom_train_ingredients.str[2:].str.split(',').explode()
boom_train_ingredients = boom_train_ingredients.str.strip()

# Calculate the count and format into dataframe
boom_train_ingredients_df = pd.DataFrame(boom_train_ingredients.value_counts())
boom_train_ingredients_df = boom_train_ingredients_df.rename(columns={'Ingredients': 'Count'})
boom_train_ingredients_df.sort_values('Count', ascending=False)
boom_train_ingredients_df = boom_train_ingredients_df.reset_index()
boom_train_ingredients_df.columns=['Ingredients', 'Count']

# Create a new column for percentage
boom_train_ingredients_df['Percent'] = round(boom_train_ingredients_df['Count'] / sum(boom_train_ingredients_df['Count']) * 100, 2)

boom_train_ingredients_df

Ingredients  Count  Percent
0           B   1872    32.72
1           S   1819    31.80
2           C   1290    22.55
3           L    390     6.82
4           V    276     4.82
5          S*     49     0.86
6          Sa     25     0.44

In [14]:
# B = Beans, S = Sugar, S* = Sweetener other than white cane or beet sugar, C = Cocoa Butter, V = Vanilla, L = Lecithin, Sa = Salt
alt.Chart(boom_train_ingredients_df).mark_bar().encode(
    x=alt.X('Count', title='Count'),
    y=alt.Y('Ingredients', sort='x', title='Ingredients')
).properties(
    width=400,
    height=200
)

alt.Chart(...)

- Here are the definitions of the ingredient symbols:
    - B = Beans
    - S = Sugar
    - S* = Sweetener other than white cane or beet sugar
    - C = Cocoa Butter
    - V = Vanilla
    - L = Lecithin
    - Sa = Salt 
    
- We also count their numbers and the percentages that occur in all the data observations, then plot a bar graph of their distribution. The beans are the main top ingredients that occur $32.72$% in all the observations, while the sugar also occurs in almost $31.80$% of all the observations. At the same time, salt and other sweetener have a significantly low percentage that shows in all the data, respectively as $0.44$% and $0.86$%.

#### **`Most_Memorable_Characteristics`**

In [15]:
# Analyse Most_Memorable_Characteristics

# Split the comma delimited text
boom_train_characteristics = train_df['Most_Memorable_Characteristics'].str.split(',').explode()

# Calculate the count and format into dataframe
boom_train_characteristics_df = pd.DataFrame(boom_train_characteristics.value_counts())
boom_train_characteristics_df = boom_train_characteristics_df.rename(columns={'Most_Memorable_Characteristics': 'Count'})
boom_train_characteristics_df.sort_values('Count', ascending=False)
boom_train_characteristics_df = boom_train_characteristics_df.reset_index()
boom_train_characteristics_df.columns=['Characteristics', 'Count']

# Create a new column for percentage
boom_train_characteristics_df['Percent'] = round(boom_train_characteristics_df['Count'] / sum(boom_train_characteristics_df['Count']) * 100, 2)

boom_train_characteristics_df

Characteristics  Count  Percent
0                       cocoa    165     3.03
1                       nutty    136     2.50
2                       sweet    133     2.44
3                      roasty    124     2.28
4                      creamy    121     2.22
...                       ...    ...      ...
1033           intense bitter      1     0.02
1034               off spicey      1     0.02
1035            intense spice      1     0.02
1036   chemical or burnt note      1     0.02
1037                blueberry      1     0.02

[1038 rows x 3 columns]

In [16]:
alt.Chart(boom_train_characteristics_df[:20]).mark_bar().encode(
    x=alt.X('Count', title='Count'),
    y=alt.Y('Characteristics', sort='x', title='Memorable Characteristics')
).properties(
    width=400,
    height=300
)

alt.Chart(...)

We split the comma-delimited "most memorable characteristics", count their numbers and the percentages that occurs in all the data observation, then plot a bar graph of their distribution. Cocoa as a main ingredient also appears to be the top flavour at $3.03$%. The "nutty" and "sweet" are the other top two flavors at $2.50$% and $2.44$% respectively. Their occurring percentage is not as much as the ingredients because the flavor is decided by the tasting reviewer. Each chocolate might taste different to the different tasters, and the flavor reviewing will be subjective and various.

## Visualizing features

#### **`Cocoa_Percent`**

- We believe one of the most effective features is `Cocoa_Percent`, so we will do a correlation visualization between it and our target value `Rating` 
- To have a better and more straightforward visualization, we will group these two features are grouped into categories.
- Based on the data owner [explanation](http://flavorsofcacao.com/review_guide.html), we will group the Rating into:
    - 4.0 - 5.0   = Outstanding
    - 3.5 - 3.9   = Highly Recommended
    - 3.0 - 3.49 = Recommended
    - 2.0 - 2.9   = Disappointing
    - 1.0 - 1.9   = Unpleasant
- We will group the cocoa percentage into:
    - '40-49%'
    - '50-59%'
    - '60-69%'
    - '70-79%'
    - '80-89%'
    - '90-100%'

In [17]:
temp_df = train_df.copy()

temp_df['Rating_c'] = pd.cut(
    x=temp_df['Rating'],
    bins=[0, 1.99, 2.99, 3.49, 3.99, 5],
    labels=['Unpleasant', 'Disappointing', 'Recommended', 'Highly Recommended', 'Outstanding']
)

temp_df['Cocoa_c'] = pd.cut(
    x=temp_df['Cocoa_Percent'],
    bins=[40, 49, 59, 69, 79, 89, 100],
    labels=['40-49%', '50-59%', '60-69%', '70-79%', '80-89%', '90-100%']
)

alt.Chart(temp_df).mark_square().encode(
    x=alt.X('Cocoa_c', title='Cocoa Category'),
    y=alt.Y('Rating_c', title='Rating Category', sort=['Unpleasant', 'Disappointing', 'Recommended', 'Highly Recommended', 'Outstanding']),
    size='count()',
    color='count()'
).properties(
    width=200,
    height=100
)

alt.Chart(...)

From the above heatmap graph, we can see the chocolate which has $70-79$% cocoa percentage is the main group and acting averagely. Most of them are recommended and highly recommended with some outstanding. A similar distribution is in the $60-69$% group, where the rating has been ordered as "Recommended, Highly Recommended, Disappointing, outstanding." However, more chocolates are considered disappointing than highly recommended in the $80-89$% cocoa group with recommended still being the top rating. In the highest cocoa percentage $90-100$% group, nearly no chocolate gets highly recommended, but some even get unpleasant ratings. The same rating pattern happens to the $50-59$% group, in which most of the chocolates in this group are recommended and disappointing. We can conclude that people do not like cocoa percentage to be too high or too low, especially too high.

#### **`Company_Location`**

- We also think the `Company_Location` is an important feature because some countries are famous for chocolate making and their chocolates might get a high rating, so we will do a correlation visualization between it and our target value `Rating`.
- Since there are many countries involved, the following plot will only show top-10 countries and group the remaining to Others.

In [18]:
temp_df2 = train_df.copy()
top10 = temp_df2['Company_Location'].value_counts()[:10].index
temp_df2['Company_Location2'] = np.where(temp_df2['Company_Location'].isin(top10), temp_df2['Company_Location'], 'Others')

temp_df2_sort = temp_df2.groupby(by = 'Company_Location2')['Rating'].agg('mean')
temp_df2_sort = temp_df2_sort.sort_values().index
temp_df2_sort = temp_df2_sort.tolist()

boxp2 = alt.Chart(temp_df2).mark_boxplot().encode(
    x=alt.X('Rating', scale=alt.Scale(domain=(0.5, 4.5))),
    y=alt.Y('Company_Location2', sort=temp_df2_sort, title='Company Location')  # sort=alt.EncodingSortField(op="mean", order='ascending'), 
)

meanp2 = boxp2.mark_circle(color='red').encode(
    x = 'mean(Rating)'
)

boxp2 + meanp2

alt.LayerChart(...)

From the above graph, we can see Australia and Switzerland get the highest rating mean of nealy $3.3$. Australia also has the highest median of $3.5$, while Switzerland only has $3.25$. This means Australia's chocolate quality is more stable with a low standard error of their rating, while Switzerland might have some high-rating chocolates as outliers but in general, its chocolate rating is lower than Australia's. 

#### **`Country_of_Bean_Origin`**

- We also think the `Country_of_Bean_Origin` is an important feature because the main ingredient of chocolate is the cocoa bean, which has various qualities among different countries. We will do a correlation visualization between it and our target value `Rating`.
- Since there are many countries involved, the following plot will only show top-10 countries and group the remaining to Others.

In [19]:
temp_df3 = train_df.copy()
top10 = temp_df3['Country_of_Bean_Origin'].value_counts()[:10].index
temp_df3['Country_of_Bean_Origin2'] = np.where(temp_df3['Country_of_Bean_Origin'].isin(top10), temp_df3['Country_of_Bean_Origin'], 'Others')

temp_df3_sort = temp_df3.groupby(by = 'Country_of_Bean_Origin2')['Rating'].agg('mean')
temp_df3_sort = temp_df3_sort.sort_values().index
temp_df3_sort = temp_df3_sort.tolist()

boxp3 = alt.Chart(temp_df3).mark_boxplot().encode(
    x=alt.X('Rating', scale=alt.Scale(domain=(0.5, 4.5))),
    y=alt.Y('Country_of_Bean_Origin2', sort=temp_df3_sort, title='Country of Bean Origin')
)

meanp3 = boxp3.mark_circle(color='red').encode(
    x = 'mean(Rating)'
)

boxp3 + meanp3

alt.LayerChart(...)

From the above graph, we can see Brazil and Nicaragua bean get highest  median value of $3.25$ with narrow error bar. They also have the highest rating mean around $3.25$, while Brazil are slightly higher than Nicaragua. Therefore, Brazil is doing the best in the chocolate bean rating. 

#### **`Company_(Manufacturer)`**

- We also think the `Company_(Manufacturer)` is an important feature because the different company made different chocolate quality, so we will do a correlation visualization between it and our target value `Rating`.
- Since there are many companies involved, the following plot will only show top-10 companies and group the remaining to Others.

In [20]:
temp_df4 = train_df.copy()
temp_df4a = temp_df4.groupby(by = 'Company_(Manufacturer)')['REF'].agg('count')
mask4 = temp_df4a[temp_df4a >= 10].index
temp_df4 = temp_df4[temp_df4['Company_(Manufacturer)'].isin(mask4)]

temp_df4_sort = temp_df4.groupby(by = 'Company_(Manufacturer)')['Rating'].agg('mean')
temp_df4_sort = temp_df4_sort.sort_values().index
temp_df4_sort = temp_df4_sort.tolist()

boxp4 = alt.Chart(temp_df4).mark_boxplot().encode(
    x=alt.X('Rating', scale=alt.Scale(domain=(0.5, 4.5))),
    y=alt.Y('Company_(Manufacturer)', sort=temp_df4_sort, title='Company (Manufacturer)')
)

meanp4 = boxp4.mark_circle(color='red').encode(
    x = 'mean(Rating)'
)

boxp4 + meanp4

alt.LayerChart(...)

From the above graph, we can see "Soma" has the highest rating mean of around $3.6$ and the highest rating median of $3.75$. However, its error bar is wide, which means that its chocolate rating is various. On the contrary, "Smooth Chocolator" are doing better with a slightly lower mean than "Soma", a narrower error bar than Soma, and the same median as $3.75$. Therefore, "Smooth Chocolatro" has stable and high chocolate rating.

## References
---

Brady Brelinski and Andrea Brelinski. 2022. "chocolate_database" Flavor of Cacao, Mahanttan Chocolate Society http://flavorsofcacao.com

Roger D. Peng and Elizabeth Matsui. 2017. "The Art of Data Science" https://bookdown.org/rdpeng/artofdatascience/